# Análise Exploratória

* Requer `./data/tpr_co2_data.csv`;

* Verificar diretório `integrate` para maiores instruções de instalação.

# Bibliotecas

In [1]:
from pyspark.sql import SparkSession
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import plotly.offline as py
import plotly.express as px
py.init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.tools as tls
from plotly.subplots import make_subplots
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import seaborn as sns
import time
import warnings
warnings.filterwarnings('ignore')

C:\Users\julia\Anaconda3\lib\site-packages\statsmodels\tools\_testing.py:19: FutureWarning:

pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.



# Leitura

In [11]:
spark = SparkSession.builder.getOrCreate()

data = spark.read.options(header='True').csv('./data/tpr_co2_data.csv')
data.show(20)

+----------+------+------+--------------------+--------------------+-------------------+------------------+------------------+
|      date|   lat|   lon|                city|             country|                tpr|           tpr_unc|               co2|
+----------+------+------+--------------------+--------------------+-------------------+------------------+------------------+
|1850-01-01| -8.84|-34.86|            Jaboatão|              Brazil|               null|              null|  284.315185546875|
|1850-01-01| -8.84|-34.86|              Recife|              Brazil|               null|              null|  284.315185546875|
|1850-01-01| -8.84|-34.86|Vitória De Santo ...|              Brazil|               null|              null|  284.315185546875|
|1850-01-01| 45.81|-72.69|            Montreal|              Canada|            -10.466|             1.445| 286.4643249511719|
|1850-01-01| 45.81|-72.69|          Sherbrooke|              Canada|            -10.466|             1.445| 286

# Análise

In [26]:
data.describe().show(100)

+-------+----------+------------------+-----------------+--------+-----------+--------------------+------------------+------------------+
|summary|      date|               lat|              lon|    city|    country|                 tpr|           tpr_unc|               co2|
+-------+----------+------------------+-----------------+--------+-----------+--------------------+------------------+------------------+
|  count|   6861761|           6861761|          6861761| 6861761|    6861761|             6734803|           6734803|           6808706|
|   mean|      null|23.001327965194324|32.41362665651364|    null|       null|  17.513312067183502|0.6556305384136641|316.93265450915146|
| stddev|      null|23.212739900958823| 74.7539339596633|    null|       null|  10.109577976111598|0.5142646885087389|30.093303272470383|
|    min|1850-01-01|              -0.8|             -0.0|A Coruña|Afghanistan|-0.00099999999999...|             0.034| 274.9664001464844|
|    max|2013-09-01|              

# Tratamento dos Dados para os Gráficos

In [2]:
dt = pd.read_csv('./data/tpr_co2_data.csv')

Iremos desconsiderar os países que são colônias, pois estes não têm seus nomes marcados, o que pode acabar atrabalhando na plotagem através do pacote plotly. 
Além disso, também desconsideraremos os valores que estão marcados como NA.

In [3]:
dt_clear = dt[~dt['country'].isin(
    ['Denmark', 'Antarctica', 'France', 'Europe', 'Netherlands',
     'United Kingdom', 'Africa', 'South America'])]

dt_clear = dt_clear.replace(
   ['Denmark (Europe)', 'France (Europe)', 'Netherlands (Europe)', 'United Kingdom (Europe)'],
   ['Denmark', 'France', 'Netherlands', 'United Kingdom'])

dt_clear = dt_clear.dropna()

# Gráficos referentes às temperaturas

## Gráfico de séries temporais

Primeiramente, obteremos os dados de interesse para tal gráfico, que são as médias globais de temperatura por ano:

In [5]:
per_date = dt_clear.groupby([dt_clear['date'].str.slice(stop=4)]).mean().reset_index()
mean_temp_world = per_date["tpr"]
mean_temp_world_uncertainty = per_date["tpr_unc"]

Abaixo temos o gráfico do Ano x Temperatura Média Global:

In [6]:
anos = np.unique(dt_clear['date'].apply(lambda x: x[:4]))

trace0 = go.Scatter(
    x = anos, 
    y = np.array(mean_temp_world) + np.array(mean_temp_world_uncertainty),
    fill= None,
    mode='lines',
    name='Uncertainty top',
    line=dict(
        color='rgb(0, 255, 255)',
    )
)

trace1 = go.Scatter(
    x = anos, 
    y = np.array(mean_temp_world) - np.array(mean_temp_world_uncertainty),
    fill='tonexty',
    mode='lines',
    name='Uncertainty bot',
    line=dict(
        color='rgb(0, 255, 255)',
    )
)

trace2 = go.Scatter(
    x = anos, 
    y = mean_temp_world,
    name='Average Temperature',
    line=dict(
        color='rgb(199, 121, 093)',
    )
)

linhas = [trace0, trace1, trace2]

layout = go.Layout(
    xaxis=dict(title='Ano'),
    yaxis=dict(title='Temperatura Média, °C'),
    title='Temperatura Média Mundial',
    showlegend = False)

fig = go.Figure(data=linhas, layout=layout)
py.iplot(fig)

Apesar de vermos oscilações na temperatura média global, vemos que há uma tendência que mostra que a mesma está aumentando conforme os anos passam. Desta forma, temos indícios de que nos últimos anos, a temperatural global tem aumentado.

## Globo Terrestre: temperatura média por país (de 1850 a 2013)

Fazendo os devidos tratamentos dos dados, calcula-se as temperaturas médias dos países, de 1850 a 2013:

In [7]:
per_country = dt_clear.groupby(['country']).mean().reset_index()
mean_temp = per_country["tpr"]

Verifica-se abaixo o mapa interativo mostrando os locais mais quentes e mais frios da Terra:

In [8]:
countries = np.unique(dt_clear['country'])

data_fig = [ dict(
        type = 'choropleth',
        locations = countries,
        z = mean_temp,
        locationmode = 'country names',
        text = countries,
        marker = dict(
            line = dict(color = 'rgb(0,0,0)', width = 1)),
            colorbar = dict(autotick = True, tickprefix = '', 
            title = 'Temperatura\nMédia,\n°C')
            )
       ]

layout = dict(
    title = 'Temperatura Média por País de 1850 a 2013',
    geo = dict(
        showframe = False,
        showocean = True,
        oceancolor = 'rgb(0,255,255)',
        projection = dict(
        type = 'orthographic',
            rotation = dict(
                    lon = 60,
                    lat = 10),
        ),
        lonaxis =  dict(
                showgrid = True,
                gridcolor = 'rgb(102, 102, 102)'
            ),
        lataxis = dict(
                showgrid = True,
                gridcolor = 'rgb(102, 102, 102)'
                )
            ),
        )

fig = dict(data=data_fig, layout=layout)
py.iplot(fig, validate=False, filename='worldmap')

Veja que aqueles países que estão em branco são aqueles que não têm registros de temperaturas.

É possível observarmos que, num geral, países localizados próximos à linha do Equador têm temperaturas mais altas quando comparados àqueles com altas latitudes.

## Temperatura Mínima por País ao Longo do Tempo

Abaixo, pega-se as temperaturas mínimas de cada país em cada ano disponível para visualizarmos se há diferenças significativas ao longo do tempo:

In [9]:
dt_countries_min = dt_clear.groupby(['country', dt_clear['date'].str.slice(stop=4)]).min().swaplevel()
dt_tpr = pd.DataFrame(data=dt_countries_min["tpr"])
dt_tpr = dt.reset_index()

start_date = '1900-01-01'
end_date = '2013-01-01'

mask = (dt_tpr['date'] > start_date) & (dt_tpr['date'] <= end_date)

dt_countrydate = dt_tpr.loc[mask]

Abaixo, temos um gráfico geoespacial indicando as temperaturas mínimas de cada país no decorrer dos anos:

In [47]:
fig = px.choropleth(dt_countrydate,
locations="country",
locationmode = "country names",
color="tpr",
hover_name="country",
range_color=(-5,32),
animation_frame="date"
)

fig.update_layout(
title_text = 'Temperatura Mínima por Ano',
title_x = 0.5,
geo=dict(
showframe = False,
showcoastlines = False),
)

fig.show() 

Veja que ao longo do tempo, a temperatura mínima dos países, principalmente daqueles próximos à linha do Equador, vão mudando conforme o tempo, indicando um aumento da temperatura.

# Gráficos referentes às concentrações de CO2

## Gráfico da concentração de dióxido de carbono no decorrer do tempo

Selecionando os dados da média de concentração de dióxido de carbono por ano, temos:

In [15]:
# per_date = dt_clear.groupby([dt_clear['date'].str.slice(stop=4)]).mean().reset_index()
mean_co2_world = per_date["co2"]

Realizando o gráfico de Ano x Concentração de gás carbônico:

In [16]:
trace0 = go.Scatter(
    x = anos, 
    y = mean_co2_world,
    name='CO2 Médio',
    line=dict(
        color='rgb(199, 121, 093)',
    )
)
linha = [trace0]

layout = go.Layout(
    xaxis=dict(title='Ano'),
    yaxis=dict(title='CO2 Médio, ppm'),
    title='CO2 Médio Mundial',
    showlegend = False)

fig = go.Figure(data=linha, layout=layout)
py.iplot(fig)

Veja que de 1850 a 1960, o comportamento a reta é um, e a partir de 1960 tal comportamento muda, de forma que a taxa de aumento da concentração de dióxido de carbono aparenta crescer mais abruptamente. Tal fato observado pode estar relacionado à pós Guerras Mundiais, momento caracterizado por altos níveis de desenvolvimento tecnológico.

## Globo Terrestre: concentração média de Dióxido de Carbono por país (1850 a 2013)

Fazendo os devidos tratamentos dos dados, calcula-se as concentrações médias de dióxido de carbono dos países, de 1850 a 2013:

In [17]:
# per_country = dt_clear.groupby(['country']).mean().reset_index()
mean_co2 = per_country["co2"]

Verifica-se abaixo o mapa interativo mostrando os locais com maiores e menores concentrações de dióxido de carbono da Terra:

In [21]:
data_fig = [ dict(
        type = 'choropleth',
        locations = countries,
        z = mean_co2,
        locationmode = 'country names',
        text = countries,
        marker = dict(
            line = dict(color = 'rgb(0,0,0)', width = 1)),
            colorbar = dict(autotick = True, tickprefix = '', 
            title = '# CO2\nMédio,\nppm')
            )
       ]

layout = dict(
    title = 'CO2 Médio por País de 1850 a 2013',
    geo = dict(
        showframe = False,
        showocean = True,
        oceancolor = 'rgb(0,255,255)',
        projection = dict(
        type = 'orthographic',
            rotation = dict(
                    lon = 60,
                    lat = 10),
        ),
        lonaxis =  dict(
                showgrid = True,
                gridcolor = 'rgb(102, 102, 102)'
            ),
        lataxis = dict(
                showgrid = True,
                gridcolor = 'rgb(102, 102, 102)'
                )
            ),
        )

fig = dict(data=data_fig, layout=layout)
py.iplot(fig, validate=False, filename='worldmap')

## Concentração Média de Dióxido de Carbono ao longo do Tempo

Calculando as médias de dióxido de carbono de cada país ao longo do tempo, temos:

In [19]:
dt_mean = dt_clear.groupby(['country', dt_clear['date'].str.slice(stop=4)]).mean().reset_index()

start_date = '1900-01-01'
end_date = '2013-01-01'

mask = (dt_mean['date'] > start_date) & (dt_mean['date'] <= end_date)

dt_countrydate = dt_mean.loc[mask]

Veja que, como pelo gráfico acima não observamos mudanças bruscas até 1960, estreitamos o intervalo de tempo para os anos de 1900 a 2013.

In [20]:
#Creating the visualization
fig = px.choropleth(dt_countrydate,
locations="country",
locationmode = "country names",
color="co2",
hover_name="country",
range_color=(290,405),
animation_frame="date"
)

fig.update_layout(
title_text = 'Concentração de CO2 por Ano (ppm)',
title_x = 0.5,
geo=dict(
showframe = False,
showcoastlines = False),
)

fig.show() 

Claramente podemos ver que desde 1900, as concentrações de dióxido de carbono em todos os países aumentaram consideravelmente.